# Dask DataFrame and cuDF on NYC Taxi CSV data

### Start Dask Cluster on an Eight-GPU DGX Machine

In [1]:
from dask_cuda import LocalCUDACluster
cluster = LocalCUDACluster()

from dask.distributed import Client
client = Client(cluster)
client

<Client: scheduler='tcp://127.0.0.1:33058' processes=8 cores=8>

### Previously we ran this to shard the files more finely for cudf.read_csv

```python
import dask.dataframe as dd
pdf = dd.read_csv('data/nyc/yellow_tripdata_2017-*.csv',
                 parse_dates=['tpep_pickup_datetime', 'tpep_dropoff_datetime'])

pdf.repartition(npartitions=100).to_csv('data/nyc/many/*.csv', index=False)
```

### Read CSV files into Dask-GPU-DataFrame

In [2]:
import dask_cudf

gdf = dask_cudf.read_csv('data/nyc/many/*.csv')
gdf.head().to_pandas()

VendorID tpep_pickup_datetime tpep_dropoff_datetime  passenger_count  \
0         1  1969-12-31 23:59:59   1969-12-31 23:59:59                1   
1         1  1969-12-31 23:59:59   1969-12-31 23:59:59                1   
2         1  1969-12-31 23:59:59   1969-12-31 23:59:59                1   
3         1  1969-12-31 23:59:59   1969-12-31 23:59:59                1   
4         2  1969-12-31 23:59:59   1969-12-31 23:59:59                1   

   trip_distance  RatecodeID  store_and_fwd_flag  PULocationID  DOLocationID  \
0           3.30           1         -2049400382           263           161   
1           0.90           1         -2049400382           186           234   
2           1.10           1         -2049400382           164           161   
3           1.10           1         -2049400382           236            75   
4           0.02           2         -2049400382           249           234   

   payment_type  fare_amount  extra  mta_tax  tip_amount  tolls_amount  \
0             1         12.5    0.0      0.5        2.00           0.0   
1             1          5.0    0.0      0.5        1.45           0.0   
2             1          5.5    0.0      0.5        1.00           0.0   
3             1          6.0    0.0      0.5        1.70           0.0   
4             2         52.0    0.0      0.5        0.00           0.0   

   improvement_surcharge  total_amount  
0                    0.3         15.30  
1                    0.3          7.25  
2                    0.3          7.30  
3                    0.3          8.50  
4                    0.3         52.80

### Time a full-pass computation

Most of the time here is spent reading data from disk and parsing it.

In [4]:
%time gdf.passenger_count.sum().compute()

CPU times: user 1.16 s, sys: 100 ms, total: 1.26 s
Wall time: 4.68 s


184464740